# Wav2vec 2.0 finetuning portuguese with the huggingface model
  

In [1]:
from datasets import load_dataset, load_metric
from datasets import load_from_disk
import argparse
from datasets import ClassLabel
import random
import pandas as pd
from IPython.display import display, HTML
import re
import json
from transformers import AutoTokenizer
from transformers import Wav2Vec2CTCTokenizer
from transformers import Wav2Vec2FeatureExtractor
from transformers import Wav2Vec2Processor
from transformers import Wav2Vec2ForCTC
import IPython.display as ipd
from IPython.display import Audio
import numpy as np
import random
import torchaudio
import librosa
import os
import json
import torch
import gc
from dataclasses import dataclass, field
from typing import Any, Dict, List, Optional, Union
import pytorch_lightning as pl
from torch.utils.data import DataLoader
from pytorch_lightning.loggers.neptune import NeptuneLogger
from fairseq.optim import adafactor

In [2]:
def speech_file_to_array_fn(batch):
  speech_array, sampling_rate = torchaudio.load(batch["path"])
  
  # batch["speech"] = speech_array[0].numpy()
  np.save(batch["path"][:-4] + '.npy', speech_array[0].numpy())
  
  batch["speech"] = batch["path"][:-4] + '.npy'
  batch["sampling_rate"] = sampling_rate
  batch["target_text"] = batch["sentence"]
  del speech_array
  gc.collect()
  return batch

def resample(batch):
  # batch["speech"] = librosa.resample(np.asarray(batch["speech"]), 48_000, 16_000)
  batch["speech"] = librosa.resample(np.array(np.load(batch["speech"])), 48_000, 16_000)
  batch["sampling_rate"] = 16_000
  return batch

def prepare_dataset(batch):
  assert (
      len(set(batch["sampling_rate"])) == 1
  ), f"Make sure all inputs have the same sampling rate of {processor.feature_extractor.sampling_rate}."

  batch["input_values"] = processor(batch["speech"], sampling_rate=batch["sampling_rate"][0]).input_values

  with processor.as_target_processor():
      batch["labels"] = processor(batch["target_text"]).input_ids
  return batch

def show_random_elements(dataset, num_examples=10):
  assert num_examples <= len(dataset), "Can't pick more elements than there are in the dataset."
  picks = []
  for _ in range(num_examples):
      pick = random.randint(0, len(dataset)-1)
      while pick in picks:
          pick = random.randint(0, len(dataset)-1)
      picks.append(pick)

  df = pd.DataFrame(dataset[picks])
  print(df)
  # display(HTML(df.to_html()))

def extract_all_chars(batch):
  all_text = " ".join(batch["sentence"])
  vocab = list(set(all_text))
  return {"vocab": [vocab], "all_text": [all_text]}

def remove_special_characters(batch):
  batch["sentence"] = re.sub(chars_to_ignore_regex, '', batch["sentence"]).lower() + " "
  return batch

# Parâmetros 

In [3]:
parser = argparse.ArgumentParser(prog="wav2vec fine-tuning") 
parser.add_argument('--pretrained', type=str, default='facebook/wav2vec2-large-xlsr-53', help='Pretrained wav2vec')
parser.add_argument('--output', type=str,
                    default="Wav2Vec2/wav2vec2-large-xlsr-portuguese/",
                    help="Output path")
parser.add_argument("-f", "--file", required=False)
args = parser.parse_args()

In [4]:
version = "wav2vec2_adam_test4" #@param {type: "string"}
lr = 1e-05#@param {type: "number"}
w_decay = 0#@param {type: "number"}
bs = 25#@param {type: "integer"}
accum_grads = 1#@param {type: "integer"}
patience = 20#@param {type: "integer"}
max_epochs = 300#@param {type: "integer"}
hold_epochs = 20#@param {type: "integer"}

# Define hyperparameters
hparams = {"version": version,
          "lr": lr,
          "w_decay": w_decay,
          "bs": bs,
          "hold_epochs":hold_epochs,
          "pretrained": args.pretrained, 
          "patience": patience,
          "accum_grads": accum_grads,
          "max_epochs": max_epochs}
hparams

{'version': 'wav2vec2_adam_test4',
 'lr': 1e-05,
 'w_decay': 0,
 'bs': 25,
 'hold_epochs': 20,
 'pretrained': 'facebook/wav2vec2-large-xlsr-53',
 'patience': 20,
 'accum_grads': 1,
 'max_epochs': 300}

## Preprocessed dataset?

In [5]:
# preprocesseds = False
preprocesseds = all([os.path.isdir('preprocessed/train')]) 
print(preprocesseds)

True


In [6]:
if not preprocesseds:
  dataset = load_dataset("common_voice", "pt", split="train+validation")
  
  dataset = dataset.train_test_split(test_size=0.15)
  
  common_voice_train = dataset['train']
  common_voice_val = dataset['test']

  common_voice_test = load_dataset("common_voice", "pt", split="test")

  columns_to_remove = ["accent", "age", "client_id", "down_votes", "gender", "locale", "segment", "up_votes"]

  common_voice_train = common_voice_train.remove_columns(columns_to_remove)
  common_voice_val = common_voice_val.remove_columns(columns_to_remove)
  common_voice_test = common_voice_test.remove_columns(columns_to_remove)

In [7]:
if not preprocesseds:
  show_random_elements(common_voice_train)

In [8]:
chars_to_ignore_regex = '[\,\?\.\!\-\;\:\"\“\%\‘\”\�]'

if not preprocesseds:
  common_voice_train = common_voice_train.map(remove_special_characters)
  common_voice_val = common_voice_val.map(remove_special_characters)
  common_voice_test = common_voice_test.map(remove_special_characters)

  show_random_elements(common_voice_train)

In [9]:
# !mkdir preprocessed

In [10]:
if not preprocesseds:
  vocab_train = common_voice_train.map(extract_all_chars, batched=True,
                                       batch_size=-1, keep_in_memory=True, remove_columns=common_voice_train.column_names)
  vocab_val = common_voice_val.map(extract_all_chars, batched=True,
                                     batch_size=-1, keep_in_memory=True, remove_columns=common_voice_test.column_names)
  vocab_test = common_voice_test.map(extract_all_chars, batched=True,
                                     batch_size=-1, keep_in_memory=True, remove_columns=common_voice_test.column_names)

  vocab_list = list(set(vocab_train["vocab"][0])| set(vocab_val["vocab"][0]) | set(vocab_test["vocab"][0]))

  vocab_dict = {v: k for k, v in enumerate(vocab_list)}
  print(vocab_dict)

  vocab_dict["|"] = vocab_dict[" "]
  del vocab_dict[" "]
  vocab_dict["[UNK]"] = len(vocab_dict)
  vocab_dict["[PAD]"] = len(vocab_dict)
  print(len(vocab_dict))

  import json
  with open('preprocessed/vocab.json', 'w') as vocab_file:
      json.dump(vocab_dict, vocab_file)

In [11]:
# Create XLSR-Wav2Vec2 Feature Extractor
tokenizer = Wav2Vec2CTCTokenizer("preprocessed/vocab.json", unk_token="[UNK]", pad_token="[PAD]", word_delimiter_token="|")

feature_extractor = Wav2Vec2FeatureExtractor(feature_size=1, sampling_rate=16000,
                                             padding_value=0.0, do_normalize=True,
                                             return_attention_mask=True)
processor = Wav2Vec2Processor(feature_extractor=feature_extractor, tokenizer=tokenizer)

In [12]:
len(processor.tokenizer)

44

In [13]:
if not preprocesseds:
  common_voice_train = common_voice_train.map(speech_file_to_array_fn,
                                              remove_columns=common_voice_train.column_names)
  common_voice_val = common_voice_val.map(speech_file_to_array_fn,
                                            remove_columns=common_voice_test.column_names)
  common_voice_test = common_voice_test.map(speech_file_to_array_fn,
                                            remove_columns=common_voice_test.column_names)

In [14]:
if not preprocesseds:
  common_voice_train = common_voice_train.map(resample, num_proc=1)
  common_voice_val = common_voice_val.map(resample, num_proc=1)
  common_voice_test = common_voice_test.map(resample, num_proc=1)

In [15]:
if not preprocesseds:
  common_voice_train.save_to_disk("preprocessed/train")
  common_voice_val.save_to_disk("preprocessed/val")
  common_voice_test.save_to_disk("preprocessed/test")

In [16]:
if preprocesseds:
  common_voice_train = load_from_disk("preprocessed/train")
  common_voice_val = load_from_disk("preprocessed/val")
  common_voice_test = load_from_disk("preprocessed/test")

In [17]:
common_voice_train = common_voice_train.map(prepare_dataset,
                                            remove_columns=common_voice_train.column_names,
                                            batch_size=1, num_proc=1, batched=True) 
common_voice_val = common_voice_val.map(prepare_dataset,
                                          remove_columns=common_voice_test.column_names,
                                          batch_size=1, num_proc=1, batched=True)
common_voice_test = common_voice_test.map(prepare_dataset,
                                          remove_columns=common_voice_test.column_names,
                                          batch_size=1, num_proc=1, batched=True)

Loading cached processed dataset at preprocessed/train/cache-967a9c7879f18d24.arrow
Loading cached processed dataset at preprocessed/val/cache-240736bc20679769.arrow
Loading cached processed dataset at preprocessed/test/cache-3e340b81b6f75b47.arrow


In [1]:
# print(common_voice_train)
# print(common_voice_train[0])

In [2]:
# print(common_voice_val)
# print(common_voice_val[0])

In [3]:
# print(common_voice_test)
# print(common_voice_test[0])

In [21]:
# stop

# Datasets and Dataloaders

In [22]:
neptune_logger = NeptuneLogger(
    api_key="eyJhcGlfYWRkcmVzcyI6Imh0dHBzOi8vYXBwLm5lcHR1bmUuYWkiLCJhcGlfdXJsIjoiaHR0cHM6Ly9hcHAubmVwdHVuZS5haSIsImFwaV9rZXkiOiJjMmJkZTg1Yy1kMjQ1LTRmMjEtYjBmYy1kMjVlMmMxODcyMTgifQ==",
    project_name='orllem/Wav2vec2')

NeptuneLogger will work in online mode


In [23]:
def show_batch(dataset, num_examples=10):
    """ Show a batch of 10 random audios from a dataset.
    """
    assert num_examples <= len(dataset), "Can't pick more elements than there are in the dataset."
    picks = []
    for _ in range(num_examples):
        pick = random.randint(0, len(dataset)-1)
        while pick in picks:
            pick = random.randint(0, len(dataset)-1)
        picks.append(pick)

    df = pd.DataFrame([dataset[pick] for pick in picks])
    display(HTML(df.to_html()))

In [24]:
class AudioDataset(torch.utils.data.Dataset):

  def __init__(self, common_voice, transform=None):
    self.common_voice = common_voice
    self.transform = transform

  def __len__(self):
    return len(self.common_voice)

  def __getitem__(self, idx):
    
    batch = self.common_voice[idx]

    input_values = batch["input_values"]
    labels = batch["labels"]
  
    return {"input_values": input_values, "labels":labels}

In [25]:
train_dataset = AudioDataset(common_voice_train)
val_dataset = AudioDataset(common_voice_val)
test_dataset = AudioDataset(common_voice_test)

In [26]:
print('Número de amostras de trenamento:', len(train_dataset))
print('Número de amostras de validação:', len(val_dataset))
print('Número de amostras de teste:', len(test_dataset))

Número de amostras de trenamento: 9440
Número de amostras de validação: 1666
Número de amostras de teste: 4641


In [27]:
data = train_dataset[0]
print(data)
audio = data["input_values"]
label = data["labels"]

print('audio:', audio)

display(Audio(data=np.asarray(audio), autoplay=True, rate=16000))
# print('audio:', type(audio))
# print('audio:', type(audio[0]))
print('label:', label)
print('label:', processor.batch_decode([label]))
# print(audio.shape)
# print(label.shape)

{'input_values': [-0.0002370849865252504, -0.0002370849865252504, -0.0002370849865252504, -0.0002370849865252504, -0.0002370849865252504, -0.0002370849865252504, -0.0002370849865252504, -0.0002370849865252504, -0.0002370849865252504, -0.0002370849865252504, -0.0002370849865252504, -0.00023708498651740326, -0.00023708498654016803, -0.00023708498650459948, -0.0002370849865436853, -0.00023708498652872943, -0.00023708498646175493, -0.00023708498670527083, -0.00023708498612901366, -0.00023708498728257601, -0.00023708498518811152, -0.00023708498870620993, -0.0002370849831543299, -0.00023708499149219066, -0.00023708497949201618, -0.00023708499604705515, -0.00023708497415177399, -0.00023708500194691927, -0.00023708496814488203, -0.00023708500728322215, -0.00023708496457843395, -0.0002370850075801311, -0.0002370849694412372, -0.00023708499531564605, -0.00023708499169107326, -0.0002370849603274147, -0.0002370850421692772, -0.00023708489184173654, -0.00023708513056905882, -0.00023708478257643026,

label: [18, 15, 18, 25, 15, 27, 14, 25, 15, 14, 15, 1, 8, 4, 14, 41, 15, 36, 14, 15, 33, 14, 26, 18, 15]
label: ['e eu sou o maior do lote']


In [28]:
show_batch(train_dataset)

In [29]:
@dataclass
class DataCollatorCTCWithPadding:
    """
    Data collator that will dynamically pad the inputs received.
    Args:
        processor (:class:`~transformers.Wav2Vec2Processor`)
            The processor used for proccessing the data.
        padding (:obj:`bool`, :obj:`str` or :class:`~transformers.tokenization_utils_base.PaddingStrategy`, `optional`, defaults to :obj:`True`):
            Select a strategy to pad the returned sequences (according to the model's padding side and padding index)
            among:
            * :obj:`True` or :obj:`'longest'`: Pad to the longest sequence in the batch (or no padding if only a single
              sequence if provided).
            * :obj:`'max_length'`: Pad to a maximum length specified with the argument :obj:`max_length` or to the
              maximum acceptable input length for the model if that argument is not provided.
            * :obj:`False` or :obj:`'do_not_pad'` (default): No padding (i.e., can output a batch with sequences of
              different lengths).
        max_length (:obj:`int`, `optional`):
            Maximum length of the ``input_values`` of the returned list and optionally padding length (see above).
        max_length_labels (:obj:`int`, `optional`):
            Maximum length of the ``labels`` returned list and optionally padding length (see above).
        pad_to_multiple_of (:obj:`int`, `optional`):
            If set will pad the sequence to a multiple of the provided value.
            This is especially useful to enable the use of Tensor Cores on NVIDIA hardware with compute capability >=
            7.5 (Volta).
    """

    processor: Wav2Vec2Processor
    padding: Union[bool, str] = True
    max_length: Optional[int] = None
    max_length_labels: Optional[int] = None
    pad_to_multiple_of: Optional[int] = None
    pad_to_multiple_of_labels: Optional[int] = None

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        input_features = [{"input_values": feature["input_values"]} for feature in features]
        label_features = [{"input_ids": feature["labels"]} for feature in features]

        batch = self.processor.pad(
            input_features,
            padding=self.padding,
            max_length=self.max_length,
            pad_to_multiple_of=self.pad_to_multiple_of,
            return_tensors="pt",
        )
        with self.processor.as_target_processor():
            labels_batch = self.processor.pad(
                label_features,
                padding=self.padding,
                max_length=self.max_length_labels,
                pad_to_multiple_of=self.pad_to_multiple_of_labels,
                return_tensors="pt",
            )

        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        batch["labels"] = labels

        return batch

In [30]:
data_collator = DataCollatorCTCWithPadding(processor=processor, padding=True)

In [31]:
batch_size = hparams["bs"]

train_dataloader = DataLoader(train_dataset, batch_size=batch_size,
                              collate_fn = data_collator,
                              shuffle=True, num_workers=8)
val_dataloader = DataLoader(val_dataset, batch_size=batch_size,
                            collate_fn = data_collator,
                            shuffle=False,  num_workers=8)
test_dataloader = DataLoader(test_dataset, batch_size=batch_size,
                             collate_fn = data_collator,
                             shuffle=False,  num_workers=8)

print('Número de minibatches de trenamento:', len(train_dataloader))
print('Número de minibatches de validação:', len(val_dataloader))
print('Número de minibatches de teste:', len(test_dataloader))

batch = next(iter(train_dataloader))
print(batch)
# x_train, y_train = next(iter(train_dataloader))
x_train, y_train = batch['input_values'], batch['labels']
print("\nDimensões dos dados de um minibatch:", x_train.size())
print("Valores mínimo e máximo: ", torch.min(x_train), torch.max(x_train))
print("Valores mínimo e máximo: ", torch.min(y_train), torch.max(y_train))
print("Tipo dos dados das imagens:         ", type(x_train))
print("Tipo das classes das imagens:       ", type(y_train))

Número de minibatches de trenamento: 378
Número de minibatches de validação: 67
Número de minibatches de teste: 186
{'input_values': tensor([[-7.2742e-05, -7.2742e-05, -7.2742e-05,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [ 1.2827e-03,  1.2827e-03,  1.2827e-03,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [ 7.6578e-05,  7.6578e-05,  7.6578e-05,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        ...,
        [-5.8362e-04, -5.8362e-04, -5.8362e-04,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [-2.6472e-04, -2.6472e-04, -2.6472e-04,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [ 2.7211e-04,  2.7211e-04,  2.7211e-04,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00]]), 'attention_mask': tensor([[1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0],
        ...,
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0]]

## Checking the batch_decode

In [32]:
print(y_train)

tensor([[  18,   15,   18,  ..., -100, -100, -100],
        [  25,    1,   15,  ..., -100, -100, -100],
        [  34,   25,   18,  ..., -100, -100, -100],
        ...,
        [  14,   15,   13,  ..., -100, -100, -100],
        [  25,    1,   15,  ..., -100, -100, -100],
        [  26,   14,   36,  ..., -100, -100, -100]])


In [33]:
y_train[y_train == -100] = processor.tokenizer.pad_token_id

label_strings = processor.batch_decode(y_train)

print('label_str:', '\n'.join(label_strings[0:10]))

label_str: e eu dise a hary que achava que ia ficar entediado até a morte
um homem na beira de uma parede prestes a cair
quero comer em algum lugar ventoso no novo méxico
onde maria foi
uma equipe em um campo de futebol
um homem na tera precisa da nosa ajuda
os negócios terão um aumento ese ano
três homens entram na praia do oceano
um homem de calças bege está esperando em uma plataforma de metrô
o que você está fazendo hoje à noite


# Creating the lightning module

In [34]:
def compute_metric_wer(pred_logits, label_ids):
  pred_ids = torch.argmax(pred_logits, axis=-1)
  # pred_ids = pred_logits
  
  pred_ids[pred_ids == -100] = processor.tokenizer.pad_token_id
  label_ids[label_ids == -100] = processor.tokenizer.pad_token_id
  
  pred_str = processor.batch_decode(pred_ids)
  print('pred_str:', '\n'.join(pred_str[0:3]))
  
  label_str = processor.batch_decode(label_ids)
  print('label_str:', '\n'.join(label_str[0:3]))
  print('------------------------------------')
  wer = wer_metric.compute(predictions=pred_str, references=label_str)

  return wer

In [35]:
wer_metric = load_metric("wer")

In [36]:
import math
import warnings
from typing import List

from torch import nn as nn
from torch.optim import Adam, Optimizer
from torch.optim.lr_scheduler import _LRScheduler


class LinearWarmupCosineAnnealingLR(_LRScheduler):
    """
    Sets the learning rate of each parameter group to follow a linear warmup schedule
    between warmup_start_lr and base_lr followed by a cosine annealing schedule between
    base_lr and eta_min.

    .. warning::
        It is recommended to call :func:`.step()` for :class:`LinearWarmupCosineAnnealingLR`
        after each iteration as calling it after each epoch will keep the starting lr at
        warmup_start_lr for the first epoch which is 0 in most cases.

    .. warning::
        passing epoch to :func:`.step()` is being deprecated and comes with an EPOCH_DEPRECATION_WARNING.
        It calls the :func:`_get_closed_form_lr()` method for this scheduler instead of
        :func:`get_lr()`. Though this does not change the behavior of the scheduler, when passing
        epoch param to :func:`.step()`, the user should call the :func:`.step()` function before calling
        train and validation methods.

    Example:
        >>> layer = nn.Linear(10, 1)
        >>> optimizer = Adam(layer.parameters(), lr=0.02)
        >>> scheduler = LinearWarmupCosineAnnealingLR(optimizer, warmup_epochs=10, max_epochs=40)
        >>> #
        >>> # the default case
        >>> for epoch in range(40):
        ...     # train(...)
        ...     # validate(...)
        ...     scheduler.step()
        >>> #
        >>> # passing epoch param case
        >>> for epoch in range(40):
        ...     scheduler.step(epoch)
        ...     # train(...)
        ...     # validate(...)
    """

    def __init__(
        self,
        optimizer: Optimizer,
        warmup_epochs: int,
        max_epochs: int,
        warmup_start_lr: float = 0.0,
        eta_min: float = 0.0,
        last_epoch: int = -1,
    ) -> None:
        """
        Args:
            optimizer (Optimizer): Wrapped optimizer.
            warmup_epochs (int): Maximum number of iterations for linear warmup
            max_epochs (int): Maximum number of iterations
            warmup_start_lr (float): Learning rate to start the linear warmup. Default: 0.
            eta_min (float): Minimum learning rate. Default: 0.
            last_epoch (int): The index of last epoch. Default: -1.
        """
        self.warmup_epochs = warmup_epochs
        self.max_epochs = max_epochs
        self.warmup_start_lr = warmup_start_lr
        self.eta_min = eta_min

        super(LinearWarmupCosineAnnealingLR, self).__init__(optimizer, last_epoch)

    def get_lr(self) -> List[float]:
        """
        Compute learning rate using chainable form of the scheduler
        """
        if not self._get_lr_called_within_step:
            warnings.warn(
                "To get the last learning rate computed by the scheduler, "
                "please use `get_last_lr()`.",
                UserWarning,
            )

        if self.last_epoch == 0:
            return [self.warmup_start_lr] * len(self.base_lrs)
        elif self.last_epoch < self.warmup_epochs:
            return [
                group["lr"] + (base_lr - self.warmup_start_lr) / (self.warmup_epochs - 1)
                for base_lr, group in zip(self.base_lrs, self.optimizer.param_groups)
            ]
        elif self.last_epoch == self.warmup_epochs:
            return self.base_lrs
        elif (self.last_epoch - 1 - self.max_epochs) % (2 * (self.max_epochs - self.warmup_epochs)) == 0:
            return [
                group["lr"] + (base_lr - self.eta_min) *
                (1 - math.cos(math.pi / (self.max_epochs - self.warmup_epochs))) / 2
                for base_lr, group in zip(self.base_lrs, self.optimizer.param_groups)
            ]

        return [
            (1 + math.cos(math.pi * (self.last_epoch - self.warmup_epochs) / (self.max_epochs - self.warmup_epochs))) /
            (
                1 +
                math.cos(math.pi * (self.last_epoch - self.warmup_epochs - 1) / (self.max_epochs - self.warmup_epochs))
            ) * (group["lr"] - self.eta_min) + self.eta_min for group in self.optimizer.param_groups
        ]

    def _get_closed_form_lr(self) -> List[float]:
        """
        Called when epoch is passed as a param to the `step` function of the scheduler.
        """
        if self.last_epoch < self.warmup_epochs:
            return [
                self.warmup_start_lr + self.last_epoch * (base_lr - self.warmup_start_lr) / (self.warmup_epochs - 1)
                for base_lr in self.base_lrs
            ]

        return [
            self.eta_min + 0.5 * (base_lr - self.eta_min) *
            (1 + math.cos(math.pi * (self.last_epoch - self.warmup_epochs) / (self.max_epochs - self.warmup_epochs)))
            for base_lr in self.base_lrs
        ]

In [37]:
class Wav2VecNet(pl.LightningModule):
    def __init__(self, *args, **kwargs):
        super().__init__()

        self.hparams = hparams

        # Note como a arquitetura esta dependente dos hiperparâmetros salvos.
        self.model = Wav2Vec2ForCTC.from_pretrained(
                    hparams["pretrained"],
                    gradient_checkpointing=True,
                    ctc_loss_reduction="mean",
                    mask_time_prob=0.01,
                    mask_time_length=10,
                    mask_feature_prob=0.01,
                    mask_feature_length=10,
                    pad_token_id=processor.tokenizer.pad_token_id,
                    vocab_size=len(processor.tokenizer)
                    )
        self.model.freeze_feature_extractor()
    
    def predict_step(self, batch, batch_idx, dataloader_idx=None):
        
        input_values, labels = batch['input_values'], batch['labels']
        attention_mask = batch['attention_mask'] 
        
        logits = self.model(input_values, attention_mask=attention_mask).logits
        pred_ids = torch.argmax(logits, dim=-1)
        return pred_ids
    
    def forward(self, input_values, attention_mask):
        logits = self.model(input_values, attention_mask=attention_mask).logits
        return logits

    def training_step(self, train_batch, batch_idx):
        
        input_values, labels = train_batch['input_values'], train_batch['labels']
        attention_mask = train_batch['attention_mask'] 
        # print('input_values', input_values.shape)
        # print('labels', labels.shape) 

        # loss ctc compute
        loss = self.model(input_values, attention_mask=attention_mask, labels=labels).loss
        # print('loss', loss)

        self.log('ctc_loss_step', loss, prog_bar=True)
        
        return loss

    def training_epoch_end(self, outputs):
        loss = torch.stack([x['loss'] for x in outputs]).mean()       

        self.log("train_loss", loss, prog_bar=True)
  
    def validation_step(self, val_batch, batch_idx):
        
        input_values, labels = val_batch['input_values'], val_batch['labels']
        attention_mask = val_batch['attention_mask'] 

        # predict 
        val_loss = self.model(input_values, attention_mask=attention_mask, labels=labels).loss

        logits = self.forward(input_values, attention_mask=attention_mask)

        # print('preds', preds.shape)
        # print('labels', labels.shape) 

        wer = compute_metric_wer(logits, labels)
        # wer = compute_metric_wer(labels, labels)

        self.log('val_loss_step', val_loss, prog_bar=True)
        self.log('val_wer_step', wer, prog_bar=True)

        return {"val_loss_step": val_loss, "val_wer_step": wer}

    def validation_epoch_end(self, outputs):
        val_loss = torch.stack([x['val_loss_step'] for x in outputs]).mean()
        val_wer = np.stack([x['val_wer_step'] for x in outputs]).mean()

        self.log("val_loss", val_loss, prog_bar=True)
        self.log("val_wer", val_wer, prog_bar=True)
  
    def test_step(self, test_batch, batch_idx):
        
        input_values, labels = test_batch['input_values'], test_batch['labels']
        attention_mask = test_batch['attention_mask']

        test_loss = self.model(input_values, attention_mask=attention_mask, labels=labels).loss

        logits = self.forward(input_values, attention_mask=attention_mask)

        wer = compute_metric_wer(logits, labels)

        self.log("test_loss_step", test_loss, prog_bar=True)
        self.log("test_wer_step", wer, prog_bar=True)
        
        # Retornamos as losses do batch para podermos fazer a média no validation_epoch_end.
        return {"test_loss_step": test_loss, "test_wer_step": wer}

    def test_epoch_end(self, outputs):
        loss = torch.stack([x['test_loss_step'] for x in outputs]).mean()
        wer = np.stack([x['test_wer_step'] for x in outputs]).mean()

        self.log("test_loss", loss, prog_bar=True)
        self.log("test_wer", wer, prog_bar=True)
    
    # learning rate warm-up
    def optimizer_step(self, epoch, batch_idx, optimizer, optimizer_idx, optimizer_closure,
        on_tpu=False, using_native_amp=False, using_lbfgs=False):
        # skip the first 500 steps
        if self.trainer.global_step < 500:
            lr_scale = min(1., float(self.trainer.global_step + 1) / 500.)
            for pg in optimizer.param_groups:
                pg['lr'] = lr_scale * self.hparams["lr"]

        # update params
        optimizer.step(closure=optimizer_closure)

    def configure_optimizers(self):  

        optimizer = torch.optim.Adam(self.parameters(),
                         lr=self.hparams["lr"],
                         weight_decay=self.hparams["w_decay"])
        
        scheduler = LinearWarmupCosineAnnealingLR(optimizer, 
                                                  eta_min=0, # final-lr
                                                  warmup_start_lr=self.hparams["lr"],
                                                  warmup_epochs=self.hparams["hold_epochs"], # hold_epochs
                                                  max_epochs=self.hparams["max_epochs"])
        
        return {'optimizer': optimizer, 'lr_scheduler': scheduler, 'monitor':'val_loss'}  

In [38]:
hparams["lr"]

1e-05

# Defining the Wav2VecNet and training

##  reload checkpoint if necessary 

In [39]:
# processor = Wav2Vec2Processor.from_pretrained(args.output+hparams["version"])

# pre_model = '/content/drive/MyDrive/Wav2Vec2/wav2vec2_test1-epoch=19-step=7559.ckpt'
# pl_model= Wav2VecNet.load_from_checkpoint(pre_model, hparams=hparams)

# trainer = pl.Trainer(resume_from_checkpoint=pre_model)

In [40]:
pl_model= Wav2VecNet(hparams=hparams)

checkpoint_path = 'Wav2Vec2/epoch=0.ckpt'
checkpoint_dir = os.path.dirname(os.path.abspath(checkpoint_path))
print(f'Files in {checkpoint_dir}: {os.listdir(checkpoint_dir)}')
print(f'Saving checkpoints to {checkpoint_dir}')
checkpoint_callback = pl.callbacks.ModelCheckpoint(prefix=hparams["version"],
                                                    dirpath=checkpoint_dir,
                                                    save_top_k=1, 
                                                    verbose=True,
                                                    monitor="val_wer", mode="min")
early_stop_callback = pl.callbacks.EarlyStopping(monitor='val_wer', patience=hparams["patience"], mode='min')
lr_monitor = pl.callbacks.LearningRateMonitor(logging_interval='step')


trainer = pl.Trainer(gpus=1, 
                     precision=16,
                     logger=neptune_logger,
                     # val_check_interval=0.25,
                     num_sanity_val_steps=0,
                     accumulate_grad_batches=hparams["accum_grads"],
                     checkpoint_callback=checkpoint_callback, 
                     callbacks=[early_stop_callback, lr_monitor],
                     max_epochs=hparams["max_epochs"])

Some weights of the model checkpoint at facebook/wav2vec2-large-xlsr-53 were not used when initializing Wav2Vec2ForCTC: ['quantizer.codevectors', 'quantizer.weight_proj.weight', 'quantizer.weight_proj.bias', 'project_q.bias', 'project_hid.bias', 'project_q.weight', 'project_hid.weight']
- This IS expected if you are initializing Wav2Vec2ForCTC from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing Wav2Vec2ForCTC from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of Wav2Vec2ForCTC were not initialized from the model checkpoint at facebook/wav2vec2-large-xlsr-53 and are newly initialized: ['lm_head.weight', 'lm_head.bias']
You should probably TRAIN this model on a down-stream task to be able to u

Files in /home/nm/phd-wav2vec2-xlsr-53/notebooks/Wav2Vec2: ['wav2vec2_adam_test2-epoch=62-step=23813.ckpt', 'wav2vec2_adam_test1-epoch=36-step=13985.ckpt', 'wav2vec2-large-xlsr-portuguese', '.ipynb_checkpoints']
Saving checkpoints to /home/nm/phd-wav2vec2-xlsr-53/notebooks/Wav2Vec2


In [41]:
trainer.fit(pl_model, train_dataloader, val_dataloader)

LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
psutil is not installed. You will not be able to abort this experiment from the UI.
psutil is not installed. Hardware metrics will not be collected.


https://app.neptune.ai/orllem/Wav2vec2/e/WAV-124



  | Name  | Type           | Params
-----------------------------------------
0 | model | Wav2Vec2ForCTC | 315 M 
-----------------------------------------
311 M     Trainable params
4.2 M     Non-trainable params
315 M     Total params
1,261.935 Total estimated model params size (MB)


/opt/conda/envs/wav2vec/lib/python3.7/site-packages/torch/_tensor.py:575: UserWarning: floor_divide is deprecated, and will be removed in a future version of pytorch. It currently rounds toward 0 (like the 'trunc' function NOT 'floor'). This results in incorrect rounding for negative values.
To keep the current behavior, use torch.div(a, b, rounding_mode='trunc'), or for actual floor division, use torch.div(a, b, rounding_mode='floor'). (Triggered internally at  /pytorch/aten/src/ATen/native/BinaryOps.cpp:467.)
  return torch.floor_divide(self, other)


pred_str: 


label_str: talvez tenha sido ontem
descobriu que as mulheres ainda são afetadas por idéias tradicionais
eu quero comida
------------------------------------
pred_str: 


label_str: eles estabeleceram iso em todos os lugares ou coreram para restaurálo
uma mulher com cabelo castanho encaracolado olha para um menu
o novo visual studio parece lindo
------------------------------------
pred_str: 


label_str: o fazendeiro trocou seu cavalo por um boi marom
a felicidade e o cérebro raramente se encontram
o rapaz acostumado a reconhecer os preságios falou com o comerciante
------------------------------------
pred_str: 


label_str: o volume não aumentaria muito mais
como podemos reconciliar este conflito
hoje a nosa casa
------------------------------------
pred_str: 


label_str: onde charlote deixou as chaves
uma pesoa em leging azul desfrutando de patinação no gelo
eu realmente acho que é importante
------------------------------------
pred_str: 


label_str: o plano ou esboç

...

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



pred_str: talvez tenha sido ontem
descobriu que as mulheres ainda são afetadas por ideias tradicionais  q
eu quero comida
label_str: talvez tenha sido ontem
descobriu que as mulheres ainda são afetadas por idéias tradicionais
eu quero comida
------------------------------------
pred_str: eles estabeleceram isso em todos os lugares ou correram para restaurálo
uma mulher com cabelo castanho e caracolado olha para um menu
o novo visual estúdio parece lindo
label_str: eles estabeleceram iso em todos os lugares ou coreram para restaurálo
uma mulher com cabelo castanho encaracolado olha para um menu
o novo visual studio parece lindo
------------------------------------
pred_str: o fazendeiro trogou seu cavalo tlumboi marrom
a felicidade e o cérebro raramente se encontram
o rapaz acostumado a reconhecer os presságios falou com o comerciante
label_str: o fazendeiro trocou seu cavalo por um boi marom
a felicidade e o cérebro raramente se encontram
o rapaz acostumado a reconhecer os preságios fa

Epoch 119, step 45359: val_wer was not in top 1


pred_str: tudo isso aconteceu entre o nascero e o pôr do sol o menino pensou
uma mulher e um cão sentamse no tronco de uma árvore
uma pequena palavra pode derrubálo
label_str: tudo iso aconteceu entre o nascer eo pôr do sol o menino pensou
uma mulher e um cão sentamse no tronco de uma árvore
uma pequena palavra pode derubálo
------------------------------------



1

In [42]:
if not os.path.isfile(args.output+hparams["version"]):
    print('saving processor to: ' + args.output+hparams["version"])
    processor.save_pretrained(args.output+hparams["version"])

saving processor to: Wav2Vec2/wav2vec2-large-xlsr-portuguese/wav2vec2_adam_test4


# Testing the best model

## Reload processor if necessary

In [43]:
# processor = Wav2Vec2Processor.from_pretrained(args.output+hparams["version"])

In [44]:
best_model = checkpoint_callback.best_model_path
# best_model = '/home/nm/phd-wav2vec2-xlsr-53/notebooks/Wav2Vec2/wav2vec2_adam_test2-epoch=33-step=12851.ckpt'
print(best_model)
test_model = Wav2VecNet.load_from_checkpoint(best_model, hparams=hparams).cuda().eval()

/home/nm/phd-wav2vec2-xlsr-53/notebooks/Wav2Vec2/wav2vec2_adam_test4-epoch=99-step=37799.ckpt


Some weights of the model checkpoint at facebook/wav2vec2-large-xlsr-53 were not used when initializing Wav2Vec2ForCTC: ['quantizer.codevectors', 'quantizer.weight_proj.weight', 'quantizer.weight_proj.bias', 'project_q.bias', 'project_hid.bias', 'project_q.weight', 'project_hid.weight']
- This IS expected if you are initializing Wav2Vec2ForCTC from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing Wav2Vec2ForCTC from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of Wav2Vec2ForCTC were not initialized from the model checkpoint at facebook/wav2vec2-large-xlsr-53 and are newly initialized: ['lm_head.weight', 'lm_head.bias']
You should probably TRAIN this model on a down-stream task to be able to u

In [45]:
trainer.test(test_model, test_dataloader)

LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


pred_str: nem um vadamem osutros infumindo os de tet um bambader osta
e diar dinheiro emprestado as pessoas da aldeira
oito
label_str: nem o radar nem os outros instrumentos detectaram o bombardeiro stealth
pedir dinheiro emprestado às pesoas da aldeia
oito
------------------------------------
pred_str: a infância é simples e bonita
existem muitas informações ricas e relevantes para referência
vá para o eroporto para enviar sua bagagem
label_str: a infância é simples e bonita
existem muitas informações ricas e relevantes para referência
vá para o aeroporto para enviar sua bagagem
------------------------------------
pred_str: estou interessado apenas do presente
ela era a prelinda zoira da aldeni
onde está o paceio
label_str: estou interesado apenas no presente
ela é a primeira noiva da aldeia
onde está o paseio
------------------------------------
pred_str: academia de belas artes de kiotkansy departamento de arte estrangeiro
a livi e a pressão econômica de deixar uma pessoa sem empre

[{'test_loss_step': 0.2182530164718628,
  'test_wer_step': 0.17233845591545105,
  'test_loss': 0.2182530164718628,
  'test_wer': 0.1723384580944666}]